# Planning Notebook

In [2]:
import math
import unittest
import numpy as np
from itertools import product
import tqdm
from tqdm import tqdm_notebook
import copy
import pickle
import time

# import gtsam
import gtsam
from gtsam import *
from gtsam.utils.test_case import GtsamTestCase

# import gtbook
import gtbook
from gtbook.display import *
from gtbook.discrete import *

# import local package
import gtsam_planner
from gtsam_planner import *

# import parser
import SASParser
from SASParser import SAS, Operator
from typing import List, Tuple, Callable, Dict, Iterable

import SasToGtsam
from SasToGtsam import SASToGTSAM

DiscreteKey = Tuple[int, int]

variables = Variables()
def pretty(obj): 
    return gtbook.display.pretty(obj, variables)

import graphviz
class show(graphviz.Source):
    """ Display an object with a dot method as a graph."""

    def __init__(self, obj):
        """Construct from object with 'dot' method."""
        # This small class takes an object, calls its dot function, and uses the
        # resulting string to initialize a graphviz.Source instance. This in turn
        # has a _repr_mimebundle_ method, which then renders it in the notebook.
        super().__init__(obj.dot())

In [3]:
sas = SAS()
sas_dir = "sas/gripper_01.sas"
sas.read_file(sas_dir)
converter = SASToGTSAM(sas)

In [4]:
# start = time.time()
# k = 12
# states = []
# mutex_factors = []
# op_factors = []
# frame_factors = []
# for i in range(k):
#     # generate state
#     state_t = converter.generate_state(i)
#     states.append(state_t)
#     # generate mutex factor for the state
#     mutex_factor_t = converter.generate_mutex_factor(state_t)
#     mutex_factors.append(mutex_factor_t)
# for j in range(len(states)-1):
#     op_key = converter.generate_operator_key(j)
#     op_factor, frame_factor = converter.generate_frame_op_factor(states[j], states[j+1], op_key)
#     op_factors.append(op_factor)
#     frame_factors.append(frame_factor)
# initial_factor = converter.generate_initial_factor(states[0])
# goal_factor = converter.generate_goal_factor(states[-1])

# graph = gtsam.DiscreteFactorGraph()
# for m_factor in mutex_factors:
#     for f in m_factor:
#         graph.push_back(f)

# graph.push_back(goal_factor)
# graph.push_back(initial_factor)

# for op_factor in op_factors:
#     graph.push_back(op_factor)

# for frame_factor in frame_factors:
#     graph.push_back(frame_factor)

# val = graph.optimize()
# end = time.time()
# assert graph(val) == 1
# print("time taken:", end - start)

In [5]:
# graph, val, k = plan(12)

In [6]:
# print(graph)

In [7]:
# graph(val)

In [8]:
# op_consts = []
# for i in range(graph.size()-1, graph.size()-k, -1):
#     op_consts.append(graph.at(i))
# val_list = []
# for op_const in reversed(op_consts):
#     print(converter.ops_names[val[op_const.operatorKey()]])

In [9]:
# converter.variables

In [10]:
start = time.time()
k = 2
states = []
mutex_factors = []
op_factors = []
frame_factors = []
for i in range(k):
    # generate state
    state_t = converter.generate_state(i)
    states.append(state_t)
    # generate mutex factor for the state
    mutex_factor_t = converter.generate_mutex_factor(state_t)
    mutex_factors.append(mutex_factor_t)

operators = []
for j in range(k-1):
    op_key = converter.generate_operator_key(j)
    operators.append(op_key)
    op_factor, frame_factor = converter.generate_frame_op_factor(states[j], states[j+1], op_key)
    op_factors.append(op_factor)
    frame_factors.append(frame_factor)
initial_factor = converter.generate_initial_factor(states[0])
goal_factor = converter.generate_goal_factor(states[-1])

graph = gtsam.DiscreteFactorGraph()
for m_factor in mutex_factors:
    for f in m_factor:
        graph.push_back(f)

# graph.push_back(goal_factor)
# graph.push_back(initial_factor)

for op_factor in op_factors:
    graph.push_back(op_factor)

for frame_factor in frame_factors:
    graph.push_back(frame_factor)

# this is where the planning happens
# enum OrderingType { COLAMD, METIS, NATURAL, CUSTOM };
# orderingType  = gtsam.Ordering.OrderingType.METIS
# dag = graph.maxProduct(orderingType)


ordering = gtsam.Ordering()
# From Initial State
# for j in range(k):
#     for state in states[j]:
#         ordering.push_back(state[0])
#     if j < k-1:
#         ordering.push_back(operators[j][0])

# From Goal State
for j in reversed(range(k)):
    if j < k-1:
        ordering.push_back(operators[j][0])
    for state in states[j]:
        ordering.push_back(state[0])

# Mixed 1/3
# for i in range(k//3):
#     for state in states[i]:
#         ordering.push_back(state[0])
#     if i < k-1:
#         ordering.push_back(operators[i][0])

# for j in range(k-1, k//3-1, -1):
#     if j < k-1:
#         ordering.push_back(operators[j][0])
#     for state in states[j]:
#         ordering.push_back(state[0])

# Mixed 1/2
# for i in range(k//2):
#     for state in states[i]:
#         ordering.push_back(state[0])
#     if i < k-1:
#         ordering.push_back(operators[i][0])

# for j in range(k-1, k//2-1, -1):
#     if j < k-1:
#         ordering.push_back(operators[j][0])
#     for state in states[j]:
#         ordering.push_back(state[0])

# Mixed 2/3
# for i in range(2*k//3):
#     for state in states[i]:
#         ordering.push_back(state[0])
#     if i < k-1:
#         ordering.push_back(operators[i][0])

# for j in range(k-1, 2*k//3-1, -1):
#     if j < k-1:
#         ordering.push_back(operators[j][0])
#     for state in states[j]:
#         ordering.push_back(state[0])

# for j in reversed(range(k)):
#     if j < k-1:
#         ordering.push_back(operators[j][0])
    
# for j in reversed(range(k)):
#     for state in states[j]:
#         ordering.push_back(state[0])

# minigraph = gtsam.DiscreteFactorGraph()

dag = graph.sumProduct(ordering)
# result = dag.argmax()

# result = graph.optimize()

end = time.time()
# assert graph(result) == 1
print("time taken:", end - start)

time taken: 3.9572744369506836


In [11]:
dag.size()

15

In [12]:
pairwise_factor = dag.at(0)

In [14]:
pairwise_factor.nrParents()

14

In [13]:
gtsam.DiscreteBayesNet(dag).at(0)

TypeError: __init__(): incompatible constructor arguments. The following argument types are supported:
    1. gtsam.gtsam.DiscreteBayesNet()

Invoked with: DiscreteLookupDAG
 
size: 15
factor 0:  g( 7 ; 0 1 2 3 4 5 6 8 9 10 11 12 13 14 ):
 Choice(14) 
 0 Choice(10) 
 0 0 Choice(8) 
 0 0 0 Leaf    0
 0 0 1 Leaf    0
 0 0 2 Leaf    0
 0 0 3 Leaf    0
 0 0 4 Choice(7) 
 0 0 4 0 Choice(1) 
 0 0 4 0 0 Choice(0) 
 0 0 4 0 0 0 Leaf    1
 0 0 4 0 0 1 Leaf    0
 0 0 4 0 1 Leaf    0
 0 0 4 0 2 Leaf    0
 0 0 4 0 3 Leaf    0
 0 0 4 0 4 Leaf    0
 0 0 4 1 Leaf    0
 0 1 Leaf    0
 0 2 Leaf    0
 1 Choice(10) 
 1 0 Choice(9) 
 1 0 0 Leaf    0
 1 0 1 Leaf    0
 1 0 2 Leaf    0
 1 0 3 Leaf    0
 1 0 4 Choice(7) 
 1 0 4 0 Choice(2) 
 1 0 4 0 0 Choice(0) 
 1 0 4 0 0 0 Leaf    1
 1 0 4 0 0 1 Leaf    0
 1 0 4 0 1 Leaf    0
 1 0 4 0 2 Leaf    0
 1 0 4 0 3 Leaf    0
 1 0 4 0 4 Leaf    0
 1 0 4 1 Leaf    0
 1 1 Leaf    0
 1 2 Leaf    0
 2 Choice(10) 
 2 0 Leaf    0
 2 1 Choice(8) 
 2 1 0 Leaf    0
 2 1 1 Le

In [16]:
states

[[(0, 2), (1, 5), (2, 5), (3, 3), (4, 3), (5, 3), (6, 3)],
 [(7, 2), (8, 5), (9, 5), (10, 3), (11, 3), (12, 3), (13, 3)]]

In [13]:
x1_t = states[0][0]
x1_tp = states[0][1]

In [14]:
x1_t

(0, 2)

In [15]:
x1_tp

(1, 5)

In [18]:
graph.optimize()

DiscreteValues{0: 0, 1: 0, 2: 1, 3: 2, 4: 2, 5: 0, 6: 0, 7: 0, 8: 0, 9: 4, 10: 2, 11: 0, 12: 0, 13: 0, 14: 5}